# Import

In [1]:
import os
import re
import sys
import csv
import json
import string
import random
import argparse
import pickle as pkl
from collections import Counter, defaultdict
from tqdm import tqdm

import numpy as np
import pandas as pd

import matplotlib.pyplot as plt

# Define

In [2]:
def load_jsonl(data_file):
    data = [json.loads(l) for l in open(data_file, "r")]
    return data


def normalize_text(s):
    """Lower text and remove punctuation, articles and extra whitespace."""
    def remove_articles(text):
        regex = re.compile(r'\b(a|an|the)\b', re.UNICODE)
        return re.sub(regex, ' ', text)
    def white_space_fix(text):
        return ' '.join(text.split())
    def remove_punc(text):
        exclude = set(string.punctuation)
        return ''.join(ch for ch in text if ch not in exclude)
    def lower(text):
        return text.lower()
    #return white_space_fix(remove_articles(remove_punc(lower(s))))
    return white_space_fix(remove_punc(lower(s)))


def get_tokens(s):
    if not s: return []
    return normalize_text(s).split()


def count_ngrams(txt, max_n):
    out_d = {}
    for n in range(1, max_n + 1):
        ngrams = zip(*[txt[i:] for i in range(n)])
        ngram2count = Counter(ngrams)
        out_d[n] = ngram2count
    return out_d

def get_ngram_counts(exs, fields, max_n=4, cache_out = None, fname = None, overwrite=False):    
    ngrams = []
    ngrams2count = defaultdict(Counter)
    
    if (not cache_out is None) and not overwrite and os.path.exists(cache_out):
        ngrams2count, ngrams = pkl.load(open(cache_out, 'rb'))
        print(f'Loaded cached ngram counts from {cache_out}')
    else:
        for ex in tqdm(exs, desc=f'Counting n-grams {fname}'):
            field2ngrams = {}
            for field in fields:
                field_toks = get_tokens(ex[field])
                field_ngrams = count_ngrams(field_toks, max_n)
                field2ngrams[field] = field_ngrams
                for n, count in field_ngrams.items():
                    ngrams2count[n] += count
            ngrams.append(field2ngrams)

        if not cache_out is None:
            pkl.dump((ngrams2count,ngrams), open(cache_out, 'wb'))
            print(f'Saved ngram counts to {cache_out}')
        
    return (ngrams2count,ngrams)

def get_length_stats(exs):
    pass

# Get Counts

In [3]:
cache_base = os.path.join('.', 'ngram_stats')

In [4]:
with open(os.path.join('.', 'all_val_data.p'), 'rb') as f:
    val_data = pkl.load(f) 

In [5]:
exs, ngram_counts, unigram_lengths = {}, {}, {}   

t = tqdm(val_data.items())
for data_key, ex_dict in t:
    t.set_description('_'.join(data_key))
    temp_ex = [{'text': text, 'label': label} for text, label in zip(ex_dict['text'], ex_dict['label'])]
    exs[data_key] = temp_ex
    ngram_counts[data_key] = get_ngram_counts(
        temp_ex,
        ['text'],
        cache_out = os.path.join(cache_base, 'counts', f"{'_'.join(data_key)}_counts.p"),
        fname = data_key
    )
    unigram_lengths[data_key] = [count_ngrams(text, 1) for text in ex_dict['text']]
        

id_val_imdb:   0%|                                                                               | 0/7 [00:00<?, ?it/s]

Loaded cached ngram counts from .\ngram_stats\counts\id_val_imdb_counts.p


Counting n-grams ('ood', 'val', 'imdb'):   1%|▍                                  | 311/25000 [00:11<1:16:47,  5.36it/s]


Counting n-grams ('ood', 'val', 'imdb'):   2%|▊                                    | 518/25000 [00:20<16:16, 25.07it/s]


Counting n-grams ('ood', 'val', 'imdb'):   3%|█                                    | 716/25000 [00:29<19:01, 21.28it/s]


...

Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  77%|████████████████▉     | 1879/2440 [00:39<00:22, 24.62it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  77%|████████████████▉     | 1882/2440 [00:39<00:22, 25.13it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  77%|████████████████▉     | 1885/2440 [00:39<00:21, 25.62it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  77%|█████████████████     | 1888/2440 [00:39<00:21, 25.26it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  78%|█████████████████     | 1891/2440 [00:39<00:21, 25.46it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  78%|█████████████████     | 1894/2440 [00:39<00:21, 25.73it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  78%|█████████████████     | 1897/2440 [00:39<00:21, 25.27it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  78%|█████████████████▏    | 1900/2440 [00:39<00:21, 25.66it/s]
Counting n-grams ('ood', 'val', 'counter

Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  85%|██████████████████▋   | 2077/2440 [00:47<00:16, 22.23it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  85%|██████████████████▊   | 2080/2440 [00:47<00:15, 22.65it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  85%|██████████████████▊   | 2083/2440 [00:47<00:15, 22.85it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  85%|██████████████████▊   | 2086/2440 [00:47<00:15, 23.09it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  86%|██████████████████▊   | 2089/2440 [00:47<00:15, 22.95it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  86%|██████████████████▊   | 2092/2440 [00:47<00:15, 22.49it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  86%|██████████████████▉   | 2095/2440 [00:47<00:15, 22.73it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  86%|██████████████████▉   | 2098/2440 [00:47<00:14, 22.96it/s]
Counting n-grams ('ood', 'val', 'counter

Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  93%|████████████████████▌ | 2275/2440 [00:55<00:07, 22.07it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  93%|████████████████████▌ | 2278/2440 [00:55<00:07, 22.23it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  93%|████████████████████▌ | 2281/2440 [00:55<00:07, 22.65it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  94%|████████████████████▌ | 2284/2440 [00:56<00:06, 22.57it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  94%|████████████████████▌ | 2287/2440 [00:56<00:06, 22.74it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  94%|████████████████████▋ | 2290/2440 [00:56<00:06, 22.50it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  94%|████████████████████▋ | 2293/2440 [00:56<00:06, 22.74it/s]
Counting n-grams ('ood', 'val', 'counterfactual-imdb'):  94%|████████████████████▋ | 2296/2440 [00:56<00:06, 21.07it/s]
Counting n-grams ('ood', 'val', 'counter

Saved ngram counts to .\ngram_stats\counts\ood_val_counterfactual-imdb_counts.p


ood_val_counterfactual-imdb: 100%|███████████████████████████████████████████████████| 7/7 [3:05:41<00:00, 1591.63s/it]
